In [7]:
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML, display
from scipy.integrate import odeint
import numpy as np

In [8]:
def plotSomeStuff(x_arrays, y_arrays, nframes=100, ax = None, fig = None):
    if ax == None or fig == None:
        fig, ax = plt.subplots()
        ax.set_xlim(-10,10)
        ax.set_ylim(-10, 10)


    marker = {}
    orbit = {}

    for ipath,(x_array, y_array) in enumerate(zip(x_arrays,y_arrays) ):
        # This is an example of how to loop over all pairs of x and y arrays.
        # The zip function takes two lists and combines them into a single list like:
        # zip( [a, b], [c, d] ) will give [ [a,c], [b,d] ]
        # The enumerate function gives you an index for each object in an iterable list.
        # So enumerate([a,b]) will give a new list [ [0,a], [1,b] ]
        marker[ipath], = ax.plot([],"o")
        orbit[ipath], = ax.plot([])

    def animate(frame_num):
        """
        """
        # Now write some code here that would loop over all pairs of the x and y arrays (see above)
        # and then use the set_data function like last week to edit each object in marker and orbit.
        for ipath,(x_array, y_array) in enumerate(zip(x_arrays,y_arrays) ):
            x = x_array[frame_num]
            y = y_array[frame_num]
            marker[ipath].set_data([x],[y]) # Modified line
            orbit[ipath].set_data([ x_array[:frame_num],y_array[:frame_num] ])
        return

    anim = FuncAnimation(fig, animate, frames=nframes, interval=20)
    display(HTML(anim.to_jshtml()))
    plt.close()

In [9]:
def ode_system(inputs,t,m):
    """
    This function represents a series of first order ODEs.

    Return: List of expressions for the first time derivative of the inputs, in order.
    """

    # Parse the inputs list to positions x,y and vector magnitudes xdot,ydot
    # But this time, let's store them in lists since there will be N
    # values of each of these for N particles.

    x = []
    y = []
    xdot = []
    ydot = []

    Fx = []
    Fy = []

    # Let's parse the inputs
    # This expects that the inputs are ordered as:
    # [x1,y1,xdot1,ydot1,x2,y2,xdot2,ydot2,...]
    for inputIndex in range(0,len(inputs),4):
        x.append(inputs[inputIndex])
        y.append(inputs[inputIndex+1])
        xdot.append(inputs[inputIndex+2])
        ydot.append(inputs[inputIndex+3])

    # Now the hard part is figuring out the sum of forces for each of these.
    # It's no longer going to be a simple xdot=Fx/m
    # We now need to sum together the gravitational forces of all of the other
    # particles.

    # Let's assume the force on particle i from particle j is
    # F_ij = -(mi*mj)/rij^2

    # So this loop is over each particle i
    for iparticle in range(len(x)):
        # The forces on particle i in the x and y directions.
        # Let's initialize them as zero and then add up the components
        Fix = 0
        Fiy = 0

        # Position of i:
        xi = x[iparticle]
        yi = y[iparticle]

        # We also need the mass of the particles... Let's assume they were
        # stored in a list in the m object.
        mi = m[iparticle]

        for jparticle in range(len(x)):
            # in this double loop, we want to skip when iparticle and jparticle
            # are the same particle. we're saying there is no gravitational self-interaction
            if iparticle==jparticle:
                continue
            # Position of j
            xj = x[jparticle]
            yj = y[jparticle]

            mj = m[jparticle]

            # Now we have all the info to calculate the distance between i and j
            rij = np.sqrt((xi-xj)**2 + (yi-yj)**2)


            # The magnitude of this force will be
            # -(m1*m2)/rij^2
            # But... we need Fx and Fy. So that's then some trig. We did some
            # of this last time:
            phi = np.arctan2(yi-yj,xi-xj)
            Fijr = -mi*mj/(rij*rij)
            Fijx = Fijr*np.cos(phi)
            Fijy = Fijr*np.sin(phi)

            # and add them to our running Fix and Fiy sums.
            # (Google the += operator in python if you haven't seen this before)
            Fix += Fijx
            Fiy += Fijy

        # Now we have all of the forces that act on particle i
        # Let's store them in a list
        Fx.append(Fix)
        Fy.append(Fiy)

    # Let's make a list of values to return
    # this will have to be ordered like:
    # [xdot1, ydot1, F1x/m1, F1y/m1, xdot2, ydot2, F2x/m2, F2y/m2, ...]

    returnlist = []
    for iparticle in range(len(x)):
        returnlist.append(xdot[iparticle])
        returnlist.append(ydot[iparticle])
        returnlist.append(Fx[iparticle]/m[iparticle])
        returnlist.append(Fy[iparticle]/m[iparticle])

    return returnlist



nframes = 50
tmax = 100
t_array = np.linspace(0,tmax,nframes)

mlist = [1,1]

solutions = odeint(ode_system, (-2,0,0,-0.4,2,0,0,0.4), t_array, args=(mlist,))

x1_array = solutions[:,0]
y1_array = solutions[:,1]

x2_array = solutions[:,4]
y2_array = solutions[:,5]


plotSomeStuff([x1_array,x2_array],[y1_array,y2_array],nframes)

*   For a completely arbitrary number of particles, the ODE_system function parses inputs — x, y, xdot, ydot — into lists of inputs corresponding to the many bodies in the system.
*   Iterating over each of these bodies by indexing over the length of one of these inputs, a loop is made to find the interaction between this particle and all others, not including itself.
*   Within this interaction calculation, the distance between particles is found and their respective masses are used to find the gravitational force between them.
*   Then, x and y components of this force are found with some trig, and outputs — xdot, ydot, Fx/m, Fy/m — are returned as lists.

In [10]:
nframes = 50
tmax = 100
t_array = np.linspace(0,tmax,nframes)

mlist = [1,1,0.009]

#solutions = odeint(ode_system, (-2,0,0,-0.4, 2,0,0,0.4, 2,-0.75,-0.4,0), t_array, args=(mlist,))
solutions = odeint(ode_system, (-2,0,0,-0.4, 2,0,0,0.4, 2,-0.75,-0.4,0), t_array, args=(mlist,))

x1_array = solutions[:,0]
y1_array = solutions[:,1]

x2_array = solutions[:,4]
y2_array = solutions[:,5]

y3_array = solutions[:,8]
x3_array = solutions[:,9]

plotSomeStuff([x1_array,x2_array,x3_array],[y1_array,y2_array,y3_array],nframes)

In [11]:
nframes = 50
tmax = 100
t_array = np.linspace(0,tmax,nframes)

mlist = [1,1,1]

#solutions = odeint(ode_system, (-2,0,0,-0.4, 2,0,0,0.4, 2,-0.75,-0.4,0), t_array, args=(mlist,))
solutions = odeint(ode_system, (-5,0,0,-0.4, 5,0,0,0.4, 2,0.75,-0.4,0), t_array, args=(mlist,))

x1_array = solutions[:,0]
y1_array = solutions[:,1]

x2_array = solutions[:,4]
y2_array = solutions[:,5]

y3_array = solutions[:,8]
x3_array = solutions[:,9]

plotSomeStuff([x1_array,x2_array,x3_array],[y1_array,y2_array,y3_array],nframes)

In [13]:
#Hand this mlist, inputs, and t

def N_body(inputs, t, mlist):
  print(f'{len(mlist)}-body problem')
  solutions = odeint(ode_system, inputs, t_array, args=(mlist,))
  list_of_x_arrays = []
  list_of_y_arrays = []
  for body in range(len(mlist)):
    x_array = solutions[:,body*4]
    y_array = solutions[:,(body*4)+1]
    list_of_x_arrays.append(x_array)
    list_of_y_arrays.append(y_array)

  plotSomeStuff(list_of_x_arrays, list_of_y_arrays, nframes)
  list_of_x_arrays.clear()
  list_of_y_arrays.clear()

  return

#mlist, inputs, and t are still given. This is not what the new function handles. It handles solutions.

#for N=3
'''nframes = 50
tmax = 100
t_array = np.linspace(0,tmax,nframes)

mlist = [1,1,0.009]

inputs = -2,0,0,-0.4, 2,0,0,0.4, 2,-0.75,-0.4,0
N_body((inputs), t_array, mlist)'''

#for N=5, lines of code do not increase
nframes = 50
tmax = 100
t_array = np.linspace(0,tmax,nframes)

mlist = [1,1,0.01,0.01,0.001]

inputs = -2,0,0,-0.4, 2,0,0,0.4, 2,-0.75,-0.4,0, -2,0.75,0.4,0, -0.75,2,0,0.4
N_body((inputs), t_array, mlist)


5-body problem


/tmp/ipykernel_387699/1347618607.py:5: ODEintWarning: Excess work done on this call (perhaps wrong Dfun type). Run with full_output = 1 to get quantitative information.
  solutions = odeint(ode_system, inputs, t_array, args=(mlist,))
